In [1]:
# imports

import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import torch as t
import torch.nn as nn
import torch.nn.functional as F

In [2]:
def generate_spiral_data(
    N: int = 100, # number of points per class
    K: int = 2, # number of classes
    R: int = 10, # radius limit
    S: int = 0.2 # noise standard deviation
):
    """
    Generate a spiral dataset
    """
    spirals = []
    for k in range(K):
        r = np.linspace(0.0, R, N)
        t = np.linspace(k * 2 * np.pi / K, (k + 4) * 2 * np.pi / K, N) + np.random.randn(N) * S
        x = r * np.sin(t)
        y = r * np.cos(t)
        spirals.append(np.vstack((x, y)).T)
    return np.stack(spirals)

In [3]:
data = generate_spiral_data(10000, 2, 10)

In [4]:
data.shape

(2, 10000, 2)

In [5]:
def plot_spiral(data, R):
    fig = go.Figure()
    fig = px.scatter(x=data[0, :, 0], y=data[0, :, 1], color_discrete_sequence=['red'])
    fig.add_scatter(x=data[1, :, 0], y=data[1, :, 1], mode='markers', marker_color='blue')
    fig.update_layout(
        xaxis=dict(
            title='x',
            showgrid=True,
            gridcolor='lightgray',
            # dtick=1,
            showline=True,
            linecolor='grey',
            zeroline=True,
            zerolinewidth=0,
            zerolinecolor='grey',
            linewidth=1,
            range=[-R, R],
            tickangle=-0,
        ),
        
        yaxis=dict(
            title='y',
            showgrid=True,
            gridcolor='lightgray',
            showline=True,
            zeroline=True,
            zerolinewidth=0,
            zerolinecolor='black',
            linewidth=1,
            linecolor='grey',
            tick0=0,
            range=[-R, R],
        ),
        )
    # Set background color to white
    fig.update_layout(plot_bgcolor='white')
    fig.update_traces(line={'width': 3.8})
    # make fig square
    fig.update_layout(
        width=500,
        height=500,
    )
    return fig

In [6]:
fig = plot_spiral(data, 10)
fig.show()

In [9]:
# Reshape and concatenate to create (x, y, c) pairs
x = data[:, :, 0].reshape(-1)
y = data[:, :, 1].reshape(-1)
y_over_x = y / (x + 1e-8)
arctan_y_over_x = np.arctan(y_over_x)
sqrt_x_squared_plus_y_squared = np.sqrt(x**2 + y**2)
c = np.repeat(np.arange(2), data.shape[1])

features = np.column_stack((x, y, y_over_x, arctan_y_over_x, sqrt_x_squared_plus_y_squared))

# Create a dataset with (featurs, c) pairs
dataset = np.column_stack((features, c))

In [10]:
# shuffle data randomly and store back in data
np.random.shuffle(dataset)

In [13]:
split = int(0.8 * dataset.shape[0])
num_features = 4

x = dataset[:, :num_features]
y = dataset[:, num_features]

x_train = x[:split]
y_train = y[:split]
x_test = x[split:]
y_test = y[split:]

In [14]:
x_train.shape, y_train.shape, x_test.shape, y_test.shape

((16000, 4), (16000,), (4000, 4), (4000,))

In [15]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
from tqdm import tqdm
import plotly.express as px

In [16]:
x_train, y_train, x_test, y_test = map(torch.tensor, (x_train, y_train, x_test, y_test))

# Create DataLoader for training and testing
train_dataset = TensorDataset(x_train.float(), y_train.long())
test_dataset = TensorDataset(x_test.float(), y_test.long())
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

In [17]:
class Network(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(Network, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.relu1 = nn.ReLU()
        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.relu2 = nn.ReLU()
        self.fc3 = nn.Linear(hidden_size, hidden_size)
        self.relu3 = nn.ReLU()
        self.fc4 = nn.Linear(hidden_size, hidden_size)
        self.relu4 = nn.ReLU()
        self.fc5 = nn.Linear(hidden_size, output_size)


    def forward(self, x):
        x = self.fc1(x)
        x = self.relu1(x)
        x = self.fc2(x)
        x = self.relu2(x)
        x = self.fc3(x)
        x = self.relu3(x)
        x = self.fc4(x)
        x = self.relu4(x)
        x = self.fc5(x)
        return x

In [21]:
input_size = 4
hidden_size = 8
output_size = 2
learning_rate = 0.001
num_epochs = 20

In [22]:
model = Network(input_size, hidden_size, output_size)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate)

In [23]:
train_losses = []
for epoch in tqdm(range(num_epochs), desc="Training", unit="epoch"):
    total_loss = 0
    for inputs, labels in train_loader:
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    train_losses.append(total_loss / len(train_loader))

Training:   0%|          | 0/20 [00:00<?, ?epoch/s]


IndexError: Target 3 is out of bounds.

In [72]:
model.eval()
correct = 0
total = 0
with torch.no_grad():
    for inputs, labels in tqdm(test_loader, desc="Testing", unit="batch"):
        outputs = model(inputs)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

accuracy = correct / total
print(f"Accuracy on test set: {accuracy * 100:.2f}%")

Testing: 100%|██████████| 125/125 [00:00<00:00, 2716.63batch/s]

Accuracy on test set: 99.98%


In [73]:
fig = px.line(x=range(1, num_epochs + 1), y=train_losses, title='Training Loss Curve')
fig.update_layout(xaxis_title='Epoch', yaxis_title='Loss')
fig.show()

In [74]:
import numpy as np
import plotly.graph_objects as go
import torch

x_grid, y_grid = np.meshgrid(np.linspace(-15, 15, 100), np.linspace(-15, 15, 100))
grid_points_tensor = torch.tensor(np.column_stack((x_grid.ravel(), y_grid.ravel())), dtype=torch.float32)

with torch.no_grad(): predictions = model(grid_points_tensor)
predicted_labels = torch.argmax(predictions, dim=1).numpy()

fig = go.Figure()

fig.add_trace(go.Contour(x=x_grid[0], y=y_grid[:, 0], z=predicted_labels.reshape(x_grid.shape), colorscale=[[0.8, 'rgb(255,200,200)'], [0.2, 'rgb(200,200,255)']], contours=dict(start=0.5, end=0.5, size=1), showscale=False, opacity=0.3))

fig.update_layout(title='Decision Boundary of the Neural Network', xaxis_title='X-axis', yaxis_title='Y-axis', showlegend=False, xaxis=dict(title='x', showgrid=True, gridcolor='lightgray', showline=True, linecolor='grey', zeroline=True, zerolinewidth=0, zerolinecolor='grey', linewidth=1, tickangle=0), yaxis=dict(title='y', showgrid=True, gridcolor='lightgray', showline=True, zeroline=True, zerolinewidth=0, zerolinecolor='black', linewidth=1, linecolor='grey', tick0=0), plot_bgcolor='white', width=500, height=500)

fig.update_traces(line={'width': 3.8})
fig.show()